# 🕹️ Analyse du marché des jeux Steam

Projet de fin de formation Jedha – Mission d’analyse pour **Ubisoft**

Objectifs principaux :

- Comprendre la structure du catalogue Steam (genres, plateformes, âges, langues, prix…)
- Identifier les **facteurs de popularité** (reviews, notes, prix…)
- Analyser l’impact de la **période COVID**
- Dégager des **opportunités marché** pour le lancement d’un nouveau jeu Ubisoft

## Plan du notebook

1.  Setup & chargement des données  
2.  Diagnostic du schéma brut (sans champs cachés)  
3.  Construction de la table principale `games_df`  
4.  Nettoyage & Feature Engineering (types, dates, reviews, COVID)  
5.  Analyse macro du marché (années, publishers, prix, âges…)  
6.  Analyse par genres (fréquence, satisfaction, plateformes)  
7.  Analyse par plateformes (Windows / Mac / Linux)  
8.  Synthèse & recommandations business pour Ubisoft

In [0]:
# 1. Setup & chargement des données depuis S3 (PySpark / Databricks)

from pyspark.sql import functions as F
from pyspark.sql import types as T
import json

# Chemin fourni par Jedha
steam_path = "s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json"

# Lecture du JSON semi-structuré
df = spark.read.json(steam_path)

print("✅ Données brutes chargées depuis :", steam_path)
print("✅ Nombre total de lignes brutes :", df.count())

✅ Données brutes chargées depuis : s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json
✅ Nombre total de lignes brutes : 55691


## 2. Diagnostic du schéma brut

Avant de construire notre table métier `games_df`, on veut vérifier :

- la structure exacte de `data` (struct imbriquée)
- la présence des champs clés : `appid`, `name`, `genre`, `publisher`, `price`, `initialprice`, `discount`, `platforms`, `release_date`, `positive`, `negative`, `languages`, `owners`, `ccu`, etc.

On affiche le schéma en JSON pour **ne cacher aucune colonne**, même si elle est imbriquée.

In [0]:
# 2.1 Schéma complet en JSON

print("🔎 SCHÉMA COMPLET (JSON compact)")
print(df.schema.json())

print("\n🔎 SCHÉMA COMPLET (JSON indenté)")
print(json.dumps(df.schema.jsonValue(), indent=2))

print("\n Schéma brut affiché.")

🔎 SCHÉMA COMPLET (JSON compact)
{"fields":[{"metadata":{},"name":"data","nullable":true,"type":{"fields":[{"metadata":{},"name":"appid","nullable":true,"type":"long"},{"metadata":{},"name":"categories","nullable":true,"type":{"containsNull":true,"elementType":"string","type":"array"}},{"metadata":{},"name":"ccu","nullable":true,"type":"long"},{"metadata":{},"name":"developer","nullable":true,"type":"string"},{"metadata":{},"name":"discount","nullable":true,"type":"string"},{"metadata":{},"name":"genre","nullable":true,"type":"string"},{"metadata":{},"name":"header_image","nullable":true,"type":"string"},{"metadata":{},"name":"initialprice","nullable":true,"type":"string"},{"metadata":{},"name":"languages","nullable":true,"type":"string"},{"metadata":{},"name":"name","nullable":true,"type":"string"},{"metadata":{},"name":"negative","nullable":true,"type":"long"},{"metadata":{},"name":"owners","nullable":true,"type":"string"},{"metadata":{},"name":"platforms","nullable":true,"type":{"fie

## 3. Construction de la table principale `games_df`

Objectif : aplatir la structure `data.*` dans une table **plate** et exploitable `games_df`.

On va :

- garder un identifiant interne (`id`) + l’`app_id` Steam
- extraire les principaux attributs d’un jeu :
  - métadonnées : `name`, `genre`, `publisher`, `developer`, `type`
  - prix : `price`, `initialprice`, `discount`
  - succès : `positive`, `negative`, `owners`, `ccu`
  - classification : `required_age`
  - accessibilité : `languages`
  - plateformes : `platforms.linux`, `platforms.mac`, `platforms.windows`
  - temporalité : `release_date`

Tous les champs seront d’abord créés en version brute (`*_raw`) pour garder la trace du format original.

In [0]:
# 3.1 Construction de la table principale des jeux à partir de df.data

def build_games_df(df):
    return (
        df
        # Identifiants
        .withColumn("id", F.col("id"))
        .withColumn("app_id", F.col("data.appid"))
        .withColumn("name", F.col("data.name"))

        # Métadonnées
        .withColumn("genre_raw", F.col("data.genre"))
        .withColumn("publisher", F.col("data.publisher"))
        .withColumn("developer", F.col("data.developer"))
        .withColumn("type", F.col("data.type"))

        # Prix & discount (brut)
        .withColumn("price_raw", F.col("data.price"))
        .withColumn("initialprice_raw", F.col("data.initialprice"))
        .withColumn("discount_raw", F.col("data.discount"))

        # Reviews & âge (brut)
        .withColumn("required_age_raw", F.col("data.required_age"))
        .withColumn("positive_raw", F.col("data.positive"))
        .withColumn("negative_raw", F.col("data.negative"))

        # Langues & owners
        .withColumn("languages_raw", F.col("data.languages"))
        .withColumn("owners_raw", F.col("data.owners"))
        .withColumn("ccu", F.col("data.ccu"))

        # Plateformes
        .withColumn("platform_linux", F.col("data.platforms.linux"))
        .withColumn("platform_mac", F.col("data.platforms.mac"))
        .withColumn("platform_windows", F.col("data.platforms.windows"))

        # Date de sortie (brute)
        .withColumn("release_date_raw", F.col("data.release_date"))
    )

games_df = build_games_df(df)

print("Table de base `games_df` construite")
print("Nombre de jeux distincts :", games_df.select("id").distinct().count())

# Aperçu contrôlé pour éviter l’affichage automatique tronqué
games_df.select(
    "id", "app_id", "name", "genre_raw", "price_raw",
    "publisher", "platform_windows", "platform_mac", "platform_linux",
    "release_date_raw"
).show(5)

Table de base `games_df` construite
Nombre de jeux distincts : 55691
+-------+-------+--------------------+--------------------+---------+--------------------+----------------+------------+--------------+----------------+
|     id| app_id|                name|           genre_raw|price_raw|           publisher|platform_windows|platform_mac|platform_linux|release_date_raw|
+-------+-------+--------------------+--------------------+---------+--------------------+----------------+------------+--------------+----------------+
|     10|     10|      Counter-Strike|              Action|      999|               Valve|            true|        true|          true|       2000/11/1|
|1000000|1000000|           ASCENXION|Action, Adventure...|      999|PsychoFlux Entert...|            true|       false|         false|      2021/05/14|
|1000010|1000010|         Crown Trick|Adventure, Indie,...|      599|Team17, NEXT Studios|            true|       false|         false|      2020/10/16|
|1000030|1000

### 3.2 Vérification des colonnes de `games_df`

On liste les colonnes et leurs types pour vérifier que la **projection depuis `data.*`** est correcte.

In [0]:
print("Colonnes de `games_df` :\n")
for col_name, col_type in games_df.dtypes:
    print(f"• {col_name:<25} {col_type}")

Colonnes de `games_df` :

• data                      struct<appid:bigint,categories:array<string>,ccu:bigint,developer:string,discount:string,genre:string,header_image:string,initialprice:string,languages:string,name:string,negative:bigint,owners:string,platforms:struct<linux:boolean,mac:boolean,windows:boolean>,positive:bigint,price:string,publisher:string,release_date:string,required_age:string,short_description:string,tags:struct<1980s:bigint,1990's:bigint,2.5D:bigint,2D:bigint,2D Fighter:bigint,2D Platformer:bigint,360 Video:bigint,3D:bigint,3D Fighter:bigint,3D Platformer:bigint,3D Vision:bigint,4 Player Local:bigint,4X:bigint,6DOF:bigint,8-bit Music:bigint,ATV:bigint,Abstract:bigint,Action:bigint,Action RPG:bigint,Action RTS:bigint,Action Roguelike:bigint,Action-Adventure:bigint,Addictive:bigint,Adventure:bigint,Agriculture:bigint,Aliens:bigint,Alternate History:bigint,Ambient:bigint,America:bigint,Animation & Modeling:bigint,Anime:bigint,Arcade:bigint,Archery:bigint,Arena Shoot

## 4. Nettoyage & Feature Engineering

Dans cette section, on transforme les champs bruts en variables analytiques propres :

- Conversion des champs numériques (`price`, `initialprice`, `discount`, `positive`, `negative`, `required_age`, `ccu`)
- Nettoyage et parsing **robuste** de la date de sortie avec ton code (multi-formats, padding, etc.)
- Création des variables temporelles : `release_year`, `release_month`, `covid_period`
- Création des variables de popularité : `total_reviews`, `positive_ratio`

L’objectif : obtenir un `games_df` directement exploitable pour toutes les analyses suivantes.

In [0]:
# 4.1 Normalisation des champs numériques (prix, reviews, âge, ccu)

games_df = (
    games_df
    # Prix : conversion en double
    .withColumn("price", F.col("price_raw").cast(T.DoubleType()))
    .withColumn("initialprice", F.col("initialprice_raw").cast(T.DoubleType()))
    .withColumn("discount", F.col("discount_raw").cast(T.DoubleType()))
    
    # Reviews : conversion en long
    .withColumn("positive", F.col("positive_raw").cast(T.LongType()))
    .withColumn("negative", F.col("negative_raw").cast(T.LongType()))
    
    # Age : garder une version string + une version numérique quand possible
    .withColumn("required_age_str", F.col("required_age_raw").cast(T.StringType()))
    .withColumn(
        "required_age",
        F.regexp_extract(F.col("required_age_str"), r"(\d+)", 1).cast(T.IntegerType())
    )
    
    # Concurrents connectés simultanément (ccu)
    .withColumn("ccu", F.col("ccu").cast(T.LongType()))
)

print("✅ Normalisation numérique effectuée")

games_df.select(
    "name", "price_raw", "price", "initialprice_raw", "initialprice",
    "discount_raw", "discount", "required_age_raw", "required_age",
    "positive_raw", "positive", "negative_raw", "negative"
).show(5)

✅ Normalisation numérique effectuée
+--------------------+---------+------+----------------+------------+------------+--------+----------------+------------+------------+--------+------------+--------+
|                name|price_raw| price|initialprice_raw|initialprice|discount_raw|discount|required_age_raw|required_age|positive_raw|positive|negative_raw|negative|
+--------------------+---------+------+----------------+------------+------------+--------+----------------+------------+------------+--------+------------+--------+
|      Counter-Strike|      999| 999.0|             999|       999.0|           0|     0.0|               0|           0|      201215|  201215|        5199|    5199|
|           ASCENXION|      999| 999.0|             999|       999.0|           0|     0.0|               0|           0|          27|      27|           5|       5|
|         Crown Trick|      599| 599.0|            1999|      1999.0|          70|    70.0|               0|           0|        4032|

In [0]:
# Ajout de colonnes dédiées : price_eur, initialprice_eur

games_df = (
    games_df
    .withColumn("price_eur", F.col("price") / 100)
    .withColumn("initialprice_eur", F.col("initialprice") / 100)
)

print("Conversion effectuée : price_eur & initialprice_eur ajoutées.")
games_df.select("name", "price", "price_eur", "initialprice", "initialprice_eur").show(5, truncate=False)


Conversion effectuée : price_eur & initialprice_eur ajoutées.
+---------------------------+------+---------+------------+----------------+
|name                       |price |price_eur|initialprice|initialprice_eur|
+---------------------------+------+---------+------------+----------------+
|Counter-Strike             |999.0 |9.99     |999.0       |9.99            |
|ASCENXION                  |999.0 |9.99     |999.0       |9.99            |
|Crown Trick                |599.0 |5.99     |1999.0      |19.99           |
|Cook, Serve, Delicious! 3?!|1999.0|19.99    |1999.0      |19.99           |
|细胞战争                   |199.0 |1.99     |199.0       |1.99            |
+---------------------------+------+---------+------------+----------------+
only showing top 5 rows



### 4.2 Nettoyage & parsing robuste de la date de sortie

Ici, on applique **exactement ton pipeline de nettoyage**, en 5 étapes :

1. Suppression des virgules (ex : `"Oct 21, 2008"` → `"Oct 21 2008"`)  
2. Remplacement des `/` par des `-` (ex : `2000/11/1` → `2000-11-1`)  
3. Padding des jours/mois à un chiffre (ex : `2000-11-1` → `2000-11-01`)  
4. Parsing multi-formats via `F.coalesce` pour gérer plusieurs formats possibles  
5. Sécurité : si imparsable, on laisse `NULL` (Spark ne lève pas d’exception, mais on garde ta logique)

On obtient ainsi une colonne propre : `release_date_parsed`.


In [0]:
# 4.2.1 Nettoyage des virgules (ex : "Oct 21, 2008" -> "Oct 21 2008")
games_df = games_df.withColumn(
    "release_date_clean",
    F.regexp_replace(F.col("release_date_raw"), ",", "")
)

# 4.2.2 Uniformisation des séparateurs "/" -> "-"
games_df = games_df.withColumn(
    "release_date_clean",
    F.regexp_replace("release_date_clean", "/", "-")
)

# 4.2.3 Padding des jours/mois à un chiffre (ex : 2000-11-1 -> 2000-11-01)
games_df = games_df.withColumn(
    "release_date_clean",
    F.regexp_replace("release_date_clean", r"-(\d)(?!\d)", r"-0$1")
)

# 4.2.4 Parsing multi-formats sécurisé
games_df = games_df.withColumn(
    "release_date_parsed",
    F.coalesce(
        F.to_date("release_date_clean", "MMM d yyyy"),
        F.to_date("release_date_clean", "MMM dd yyyy"),
        F.to_date("release_date_clean", "yyyy-MM-dd"),
        F.to_date("release_date_clean", "dd MMM yyyy"),
        F.to_date("release_date_clean", "d MMM yyyy")
    )
)

# 4.2.5 Sécurité finale : laisser NULL si imparsable, sans lever d'exception
games_df = games_df.withColumn(
    "release_date_parsed",
    F.when(F.col("release_date_parsed").isNull(), None)
     .otherwise(F.col("release_date_parsed"))
)

print("✅ Nettoyage + parsing des dates terminé")

display(
    games_df.select(
        "release_date_raw", "release_date_clean", "release_date_parsed"
    ).limit(20)
)

✅ Nettoyage + parsing des dates terminé


release_date_raw release_date_clean release_date_parsed 2000/11/1 2000-11-01 2000-11-01 2021/05/14 2021-05-14 2021-05-14 2020/10/16 2020-10-16 2020-10-16 2020/10/14 2020-10-14 2020-10-14 2019/03/30 2019-03-30 2019-03-30 2019/06/24 2019-06-24 2019-06-24 2019/01/24 2019-01-24 2019-01-24 2019/04/8 2019-04-08 2019-04-08 2019/01/6 2019-01-06 2019-01-06 2021/09/9 2021-09-09 2021-09-09 2019/12/17 2019-12-17 2019-12-17 2021/02/16 2021-02-16 2021-02-16 2019/01/3 2019-01-03 2019-01-03 2019/02/1 2019-02-01 2019-02-01 2019/11/22 2019-11-22 2019-11-22 2019/05/24 2019-05-24 2019-05-24 2019/02/4 2019-02-04 2019-02-04 2021/12/5 2021-12-05 2021-12-05 2019/02/11 2019-02-11 2019-02-11 2019/03/21 2019-03-21 2019-03-21

### 4.3 Variables temporelles dérivées & période COVID

À partir de `release_date_parsed`, on dérive :

- `release_year` : année de sortie
- `release_month` : mois de sortie
- `covid_period` :
  - `pre_covid` : avant 2019
  - `covid` : entre 2019 et 2021 inclus
  - `post_covid` : après 2021
  - `unknown` : dates manquantes ou imparsables

In [0]:
# 4.3.1 Création des variables temporelles

games_df = games_df.withColumn("release_year", F.year("release_date_parsed"))
games_df = games_df.withColumn("release_month", F.month("release_date_parsed"))

COVID_START_YEAR = 2019
COVID_END_YEAR = 2021

games_df = games_df.withColumn(
    "covid_period",
    F.when(F.col("release_year").isNull(), F.lit("unknown"))
     .when(F.col("release_year") < COVID_START_YEAR, F.lit("pre_covid"))
     .when(
         (F.col("release_year") >= COVID_START_YEAR) &
         (F.col("release_year") <= COVID_END_YEAR),
         F.lit("covid")
     )
     .otherwise(F.lit("post_covid"))
)

print("✅ Variables temporelles créées : release_year, release_month, covid_period")

games_df.select(
    "name", "release_date_raw", "release_date_parsed",
    "release_year", "release_month", "covid_period"
).show(5)

✅ Variables temporelles créées : release_year, release_month, covid_period
+--------------------+----------------+-------------------+------------+-------------+------------+
|                name|release_date_raw|release_date_parsed|release_year|release_month|covid_period|
+--------------------+----------------+-------------------+------------+-------------+------------+
|      Counter-Strike|       2000/11/1|         2000-11-01|        2000|           11|   pre_covid|
|           ASCENXION|      2021/05/14|         2021-05-14|        2021|            5|       covid|
|         Crown Trick|      2020/10/16|         2020-10-16|        2020|           10|       covid|
|Cook, Serve, Deli...|      2020/10/14|         2020-10-14|        2020|           10|       covid|
|            细胞战争|      2019/03/30|         2019-03-30|        2019|            3|       covid|
+--------------------+----------------+-------------------+------------+-------------+------------+
only showing top 5 rows



### 4.4 Variables de popularité : `total_reviews` & `positive_ratio`

On reconstruit proprement les indicateurs de popularité :

- `total_reviews` = `positive + negative`
- `positive_ratio` = `positive / total_reviews` (quand `total_reviews > 0`)

Ces deux variables seront utilisées pour :

- identifier les jeux “stars”
- comparer l’attractivité des genres
- faire des filtres par volume (éviter les jeux avec 3 reviews et un 100 % trompeur)

In [0]:
# 4.4.1 Reconstruction sûre des colonnes de reviews

games_df = (
    games_df
    .withColumn("positive", F.col("positive").cast(T.LongType()))
    .withColumn("negative", F.col("negative").cast(T.LongType()))
    .withColumn(
        "total_reviews",
        (F.col("positive") + F.col("negative")).cast(T.LongType())
    )
    .withColumn(
        "positive_ratio",
        F.when(F.col("total_reviews") > 0,
               F.col("positive").cast(T.DoubleType()) / F.col("total_reviews"))
         .otherwise(None)
    )
)

print("Colonnes reviews reconstruites : positive, negative, total_reviews, positive_ratio")

games_df.select(
    "name", "positive", "negative", "total_reviews", "positive_ratio"
).show(5)

Colonnes reviews reconstruites : positive, negative, total_reviews, positive_ratio
+--------------------+--------+--------+-------------+------------------+
|                name|positive|negative|total_reviews|    positive_ratio|
+--------------------+--------+--------+-------------+------------------+
|      Counter-Strike|  201215|    5199|       206414|0.9748127549487923|
|           ASCENXION|      27|       5|           32|           0.84375|
|         Crown Trick|    4032|     646|         4678|0.8619067977768277|
|Cook, Serve, Deli...|    1575|     115|         1690|0.9319526627218935|
|            细胞战争|       0|       1|            1|               0.0|
+--------------------+--------+--------+-------------+------------------+
only showing top 5 rows



### 4.5 Résumé du `games_df` final (base d’analyse)

On vérifie maintenant que `games_df` contient :

- les colonnes métier attendues,
- les variables dérivées prêtes pour l’EDA :

  - `release_year`, `release_month`, `covid_period`
  - `total_reviews`, `positive_ratio`
  - `platform_windows`, `platform_mac`, `platform_linux`
  - `price`, `discount`, `required_age`

In [0]:
print("Schéma final de `games_df` (colonnes principales) :\n")

for col_name in [
    "id", "app_id", "name", "genre_raw", "publisher", "developer", "type",
    "price", "initialprice", "discount",
    "required_age_str", "required_age",
    "positive", "negative", "total_reviews", "positive_ratio",
    "languages_raw", "owners_raw", "ccu",
    "platform_windows", "platform_mac", "platform_linux",
    "release_date_raw", "release_date_parsed", "release_year", "release_month", "covid_period"
]:
    if col_name in games_df.columns:
        print(f"• {col_name}")

print("\n`games_df` est prêt pour l’analyse.")
games_df.select(
    "name", "genre_raw", "price", "discount",
    "release_year", "covid_period",
    "total_reviews", "positive_ratio",
    "platform_windows", "platform_mac", "platform_linux"
).show(5, truncate=False)


Schéma final de `games_df` (colonnes principales) :

• id
• app_id
• name
• genre_raw
• publisher
• developer
• type
• price
• initialprice
• discount
• required_age_str
• required_age
• positive
• negative
• total_reviews
• positive_ratio
• languages_raw
• owners_raw
• ccu
• platform_windows
• platform_mac
• platform_linux
• release_date_raw
• release_date_parsed
• release_year
• release_month
• covid_period

`games_df` est prêt pour l’analyse.
+---------------------------+-----------------------------------+------+--------+------------+------------+-------------+------------------+----------------+------------+--------------+
|name                       |genre_raw                          |price |discount|release_year|covid_period|total_reviews|positive_ratio    |platform_windows|platform_mac|platform_linux|
+---------------------------+-----------------------------------+------+--------+------------+------------+-------------+------------------+----------------+------------+--------

# 5. Analyse Macro du Marché Steam

Dans cette section, nous analysons :

- La répartition des jeux par plateforme  
- Le volume de sorties par année  
- L’impact des périodes COVID  
- Les publishers les plus prolifiques  
- La distribution des prix  
- Les tranches d’âge (classification PEGI “like”)  
- Les langues les plus représentées

Ces analyses servent à comprendre les tendances globales du marché pour guider Ubisoft dans le lancement d’un nouveau jeu.

In [0]:
# 5.1 — Répartition des jeux par plateforme
platform_counts = (
    games_df.select(
        F.col("platform_windows").alias("Windows"),
        F.col("platform_mac").alias("Mac"),
        F.col("platform_linux").alias("Linux")
    )
)

windows_count = platform_counts.filter("Windows = true").count()
mac_count = platform_counts.filter("Mac = true").count()
linux_count = platform_counts.filter("Linux = true").count()

print("🎮 Répartition des jeux par plateforme :")
print(f"• Windows : {windows_count}")
print(f"• macOS   : {mac_count}")
print(f"• Linux   : {linux_count}")

# Vue Databricks (pour graphiques pie chart)
display(platform_counts)

🎮 Répartition des jeux par plateforme :
• Windows : 55676
• macOS   : 12770
• Linux   : 8458


Windows Mac Linux true true true true false false true false false true true false true false false true true false true false false true false false true true false true false false true false false true false false true false false true false false true false false true false false true true true true true true true false false true false false true false false true false false true true true true true true true true true true true false true false false true true true true false false true true true true false false true false false true true false true false false true false false true false false true false false true false false true false false true false false true true false true true false true false false true false false true false false true false false true true false true false false true true true true true true true false false true false false true false false true false false true false false true false false true false false true true false true true false true true false true false false true true false true false false true false false true false false true false false true false false true false false true true true true false false true false false true false false true false false true false false true false false true false false true false false true true false true false false true false false true false false true false false true false false true false false true false false true false false true false false true false false true false true true false false true false false true false false true true true true false false true true true true false false true false false true false false true false false true true true true true false true false false true true false true false false true false false true true true true false false true false false true false false true false false true false false true false false true true false true true false true false false true false false true false false true false false true false false true false false true true false true false false true false false true false false true false false true false false true true false true false true true true false true false false true true false true true true true false false true false false true true true true false false true false false true false false true false false true false false true true false true false false true false false true false false true false true true true false true true true true true true true true false true false false true false false true false false true false false true true false true false false true false false true false false true false false true false false true true true true true false true false false true false false true false false true true true true false false true false false true false false true false false true false false true false false true false false true false false true false false true true false true true false true false false true false false true false false true false false true false false true false false true false false true true true true true false true true false true true false true false false true true false true false false true false false true true true true true true true true false true false false true true false true true false true false false true false false true false false true false false true false false true true false true false false true false false true false false true false false true true true true false false true false false true false false true false false true true true true false false true false false true false false true false false true true false true false false true false false true false false true false true true false false true false false true true false true false false true false false true false false true false false true false false true false false true false false true false false true false false true false false true true false true false false true false false true true false true false fals

In [0]:
# 5.2 — Nombre de sorties par année
release_per_year = (
    games_df.groupBy("release_year")
            .count()
            .orderBy("release_year")
)

display(release_per_year)

release_per_year.show(10)

release_year count null 222 1997 2 1998 1 1999 3 2000 2 2001 4 2002 1 2003 3 2004 6 2005 6 2006 61 2007 98 2008 159 2009 309 2010 281 2011 267 2012 344 2013 469 2014 1550 2015 2566 2016 4176 2017 6006 2018 7663 2019 6949 2020 8287 2021 8805 2022 7451

+------------+-----+
|release_year|count|
+------------+-----+
|        null|  222|
|        1997|    2|
|        1998|    1|
|        1999|    3|
|        2000|    2|
|        2001|    4|
|        2002|    1|
|        2003|    3|
|        2004|    6|
|        2005|    6|
+------------+-----+
only showing top 10 rows



In [0]:
# 5.3 — Impact de la période COVID
covid_counts = (
    games_df.groupBy("covid_period")
            .count()
            .orderBy("covid_period")
)

print("Sorties par période COVID :")
display(covid_counts)

Sorties par période COVID :


covid_period count covid 24041 post_covid 7451 pre_covid 23977 unknown 222

In [0]:
# 5.4 — Publishers les plus prolifiques
publisher_counts = (
    games_df.groupBy("publisher")
            .count()
            .orderBy(F.desc("count"))
            .limit(50)
)

print("Top 50 publishers Steam par nombre de sorties :")
display(publisher_counts)

publisher_counts.show(5)

Top 50 publishers Steam par nombre de sorties :


publisher count Big Fish Games 422 8floor 202 SEGA 165 Strategy First 151 Square Enix 141 Choice of Games 140 HH-Games 132 Sekai Project 132 132 Ubisoft 127 Laush Studio 126 THQ Nordic 125 Alawar Entertainment 107 Fulqrum Publishing 104 Plug In Digital 101 Ziggurat 100 Slitherine Ltd. 99 Sokpop Collective 99 Devolver Digital 98 KOEI TECMO GAMES CO., LTD. 90 Reforged Group 89 Electronic Arts 88 Komodo 87 PLAYISM 87 SA Industry 87 Microids 84 Piece Of Voxel 81 Hosted Games 79 Kagura Games 79 Boogygames Studios 78 Artifex Mundi 75 tinyBuild 72 Daedalic Entertainment 72 Blender Games 71 BANDAI NAMCO Entertainment 69 Paradox Interactive 69 Tero Lunkka 68 2K 67 My Way Games 66 ESDigital Games 64 Garage Games 62 MAGIX Software GmbH 62 Nacon 60 Forever Entertainment S. A. 60 RewindApp 59 Ripknot Systems 55 United Independent Entertainment 55 Bethesda Softworks 55 Back To Basics Gaming 54 Hede 54

+--------------+-----+
|     publisher|count|
+--------------+-----+
|Big Fish Games|  422|
|        8floor|  202|
|          SEGA|  165|
|Strategy First|  151|
|   Square Enix|  141|
+--------------+-----+
only showing top 5 rows



In [0]:
# 5.5 — Distribution des prix
price_dist = (
    games_df
    .select("price")
    .filter("price IS NOT NULL AND price > 0")
)

display(price_dist)

price_dist.summary().show()

price 999.0 999.0 599.0 1999.0 199.0 799.0 1299.0 299.0 1399.0 99.0 1699.0 2499.0 499.0 999.0 699.0 99.0 999.0 299.0 1999.0 1199.0 99.0 1499.0 99.0 499.0 799.0 399.0 198.0 699.0 699.0 199.0 1999.0 99.0 1599.0 1499.0 99.0 1299.0 1999.0 1099.0 699.0 199.0 699.0 599.0 499.0 499.0 499.0 999.0 999.0 299.0 499.0 1699.0 999.0 199.0 199.0 799.0 899.0 1299.0 399.0 99.0 1499.0 99.0 1499.0 99.0 899.0 299.0 99.0 349.0 999.0 99.0 1699.0 799.0 1999.0 799.0 99.0 599.0 499.0 299.0 999.0 399.0 399.0 399.0 199.0 499.0 499.0 1199.0 199.0 399.0 799.0 999.0 499.0 99.0 299.0 199.0 2999.0 99.0 1499.0 1499.0 999.0 599.0 999.0 199.0 999.0 2499.0 1499.0 99.0 499.0 199.0 99.0 1499.0 3999.0 99.0 99.0 699.0 999.0 999.0 399.0 1099.0 99.0 799.0 3999.0 499.0 5999.0 199.0 299.0 99.0 599.0 1699.0 699.0 799.0 999.0 199.0 499.0 99.0 1499.0 299.0 299.0 99.0 1999.0 599.0 499.0 1899.0 99.0 299.0 99.0 99.0 499.0 1999.0 399.0 799.0 599.0 1299.0 299.0 599.0 1499.0 599.0 1299.0 1299.0 1199.0 1299.0 299.0 2999.0 399.0 99.0 1499.0 799.0 999.0 1599.0 150.0 899.0 2499.0 199.0 299.0 599.0 499.0 1499.0 99.0 1199.0 999.0 149.0 2499.0 199.0 999.0 99.0 99.0 499.0 99.0 699.0 499.0 299.0 699.0 699.0 699.0 499.0 99.0 699.0 399.0 31.0 99.0 2499.0 999.0 899.0 299.0 199.0 699.0 99.0 199.0 5999.0 199.0 599.0 99.0 399.0 299.0 499.0 54.0 399.0 1124.0 199.0 999.0 1499.0 199.0 99.0 999.0 999.0 399.0 499.0 699.0 699.0 999.0 799.0 699.0 599.0 199.0 499.0 499.0 999.0 399.0 99.0 1099.0 199.0 99.0 499.0 999.0 199.0 1299.0 99.0 399.0 99.0 199.0 99.0 99.0 999.0 99.0 999.0 489.0 599.0 99.0 499.0 99.0 199.0 559.0 399.0 299.0 599.0 599.0 99.0 1199.0 1999.0 499.0 1199.0 1999.0 99.0 499.0 599.0 199.0 199.0 90.0 5999.0 99.0 399.0 999.0 999.0 2999.0 2999.0 499.0 2499.0 699.0 99.0 999.0 99.0 599.0 259.0 99.0 299.0 499.0 499.0 999.0 99.0 199.0 1299.0 799.0 41.0 399.0 1999.0 499.0 1499.0 99.0 199.0 199.0 399.0 499.0 399.0 499.0 99.0 199.0 499.0 999.0 99.0 999.0 799.0 99.0 1199.0 199.0 199.0 999.0 179.0 499.0 499.0 99.0 199.0 999.0 199.0 999.0 99.0 1299.0 499.0 399.0 99.0 1099.0 799.0 99.0 1499.0 299.0 1999.0 99.0 299.0 1199.0 3999.0 2499.0 599.0 299.0 799.0 699.0 1999.0 499.0 999.0 1499.0 499.0 99.0 199.0 999.0 299.0 99.0 599.0 2499.0 599.0 599.0 1999.0 999.0 1499.0 399.0 99.0 199.0 1999.0 199.0 1499.0 599.0 499.0 99.0 44.0 999.0 3499.0 399.0 1299.0 499.0 799.0 99.0 499.0 64.0 2999.0 99.0 99.0 2499.0 499.0 199.0 999.0 799.0 499.0 1999.0 99.0 999.0 499.0 299.0 99.0 99.0 4499.0 399.0 399.0 2999.0 999.0 1399.0 2499.0 449.0 599.0 1499.0 1499.0 799.0 99.0 999.0 199.0 499.0 1399.0 299.0 1999.0 1999.0 699.0 399.0 199.0 199.0 1499.0 99.0 2999.0 599.0 999.0 999.0 1299.0 300.0 3499.0 599.0 999.0 599.0 799.0 399.0 1499.0 399.0 299.0 99.0 799.0 299.0 299.0 99.0 799.0 599.0 299.0 999.0 99.0 299.0 99.0 399.0 1999.0 99.0 799.0 999.0 799.0 499.0 99.0 99.0 999.0 999.0 799.0 299.0 1999.0 199.0 399.0 1199.0 699.0 599.0 699.0 999.0 499.0 499.0 99.0 99.0 499.0 99.0 799.0 249.0 999.0 1299.0 1499.0 1299.0 649.0 1999.0 99.0 699.0 1999.0 999.0 1999.0 999.0 1499.0 1499.0 1499.0 399.0 1999.0 499.0 1999.0 1499.0 1199.0 499.0 990.0 499.0 5999.0 1299.0 28.0 499.0 499.0 299.0 1499.0 199.0 499.0 99.0 1599.0 999.0 999.0 1199.0 1999.0 399.0 499.0 1299.0 1999.0 2999.0 399.0 509.0 1499.0 299.0 1999.0 999.0 1599.0 2999.0 1999.0 299.0 199.0 2499.0 1199.0 299.0 299.0 2499.0 199.0 999.0 999.0 699.0 1199.0 99.0 199.0 299.0 499.0 199.0 699.0 299.0 399.0 299.0 499.0 299.0 599.0 599.0 1999.0 149.0 1999.0 1999.0 1999.0 1999.0 199.0 1199.0 99.0 1399.0 499.0 2999.0 399.0 599.0 699.0 1899.0 99.0 999.0 799.0 499.0 1999.0 1499.0 1499.0 499.0 399.0 1499.0 1169.0 1499.0 1499.0 399.0 1799.0 999.0 499.0 1199.0 1999.0 99.0 399.0 999.0 420.0 99.0 599.0 1499.0 499.0 499.0 1499.0 899.0 999.0 1799.0 1799.0 1999.0 199.0 1199.0 99.0 499.0 499.0 899.0 2999.0 199.0 1999.0 499.0 99.0 499.0 1999.0 1299.0 1199.0 899.0 999.0 199.0 1499.0 999.0 99.0 2999.0 999.0 1999.0 99.0 1199.0 699.0 1999.0 99.0 199.0 3999.0 1699.0 199.0 999.0 99.0 199.0 499.0 1199.0 1399.0 599.0 99.0 

Databricks visualization. Run in Databricks to view.

+-------+------------------+
|summary|             price|
+-------+------------------+
|  count|             47911|
|   mean| 898.8544175659034|
| stddev|1129.6532352011948|
|    min|              28.0|
|    25%|             299.0|
|    50%|             599.0|
|    75%|            1000.0|
|    max|           99900.0|
+-------+------------------+



In [0]:
# 5.6 — Jeux en promotion
discounted_games = games_df.filter("discount > 0")
discounted_percentage = discounted_games.count() / games_df.count() * 100

print(f"Jeux actuellement en promotion : {discounted_games.count()} "
      f"({discounted_percentage:.2f} %)")

Jeux actuellement en promotion : 2518 (4.52 %)


In [0]:
# 5.7 — Classification par âge (PEGI-like)
age_dist = (
    games_df
    .select("required_age")
)

print("Répartition des jeux par âge :")
display(age_dist)

age_dist.groupBy("required_age").count().orderBy("required_age").show()

Répartition des jeux par âge :


required_age 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 12 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 16 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 17 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 12 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 10 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 7 0 0 0 0 0 0 0 16 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 12 0 0 0 0 0 0 0 0 0 0 0 0 0 15 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 17 0 0 0 0 0 0 0 0 0

+------------+-----+
|required_age|count|
+------------+-----+
|           0|55030|
|           3|    3|
|           5|    1|
|           6|    4|
|           7|    3|
|           8|    3|
|           9|    1|
|          10|    7|
|          12|   32|
|          13|   26|
|          14|   10|
|          15|  265|
|          16|   38|
|          17|   38|
|          18|  223|
|          20|    1|
|          21|    1|
|          35|    1|
|         180|    4|
+------------+-----+



In [0]:
# 5.8 — Nombre de langues supportées
# Création array de langues si pas encore fait
games_df = games_df.withColumn(
    "languages_array",
    F.split(F.col("languages_raw"), ",")
)

games_df = games_df.withColumn(
    "num_languages",
    F.size("languages_array")
)

languages_dist = games_df.select("num_languages")

print("Diversité linguistique des jeux Steam :")
display(languages_dist)

languages_dist.groupBy("num_languages").count().orderBy("num_languages").show()

Diversité linguistique des jeux Steam :


num_languages 8 3 9 1 1 5 3 3 1 3 1 2 1 1 1 5 1 29 1 1 9 1 1 2 8 1 1 1 1 1 12 1 2 2 1 3 3 5 3 6 2 1 1 1 1 2 5 1 1 1 1 1 7 1 1 5 1 2 1 4 10 4 1 1 1 1 7 3 9 1 3 1 26 2 3 1 1 2 1 2 5 3 3 1 1 2 2 1 1 1 1 1 1 1 1 2 9 1 1 7 1 1 1 1 1 1 3 1 1 4 2 2 2 29 1 2 1 16 1 1 7 15 2 2 5 1 2 1 12 3 1 29 1 1 1 10 1 1 1 1 1 2 2 1 1 7 7 1 1 2 1 1 1 4 1 2 3 5 2 6 29 5 2 3 11 1 5 12 2 1 2 1 1 1 10 12 7 3 1 12 5 2 1 9 4 16 17 2 16 1 1 1 1 3 2 1 8 1 3 1 1 11 6 1 1 1 2 1 2 2 3 7 2 3 1 9 1 1 2 1 1 2 1 2 3 1 1 1 1 1 29 1 6 8 29 1 1 3 2 4 2 29 1 1 29 4 1 1 1 6 1 4 2 2 1 1 3 1 3 3 8 1 9 4 1 1 6 3 3 2 1 2 3 4 9 1 1 1 29 1 1 1 2 1 1 2 1 2 23 2 1 1 1 1 9 6 1 1 3 2 1 1 5 1 1 1 3 2 1 3 10 1 1 2 5 1 2 1 1 3 1 2 1 11 1 7 1 1 4 1 2 1 18 1 1 1 1 1 2 1 1 2 1 1 1 3 1 2 1 3 1 1 1 1 29 1 1 6 1 1 1 1 1 2 2 4 27 2 9 10 1 4 4 1 1 2 1 1 2 3 1 1 3 7 3 3 1 1 1 1 12 1 1 1 1 1 1 6 1 1 4 1 3 1 6 4 6 1 1 1 1 2 6 1 1 2 10 1 2 2 1 2 1 10 2 1 1 2 2 5 2 3 1 1 1 3 2 1 2 1 1 1 22 1 1 1 1 1 1 6 1 1 1 1 2 2 1 1 1 11 1 1 12 1 1 1 2 1 1 1 27 27 1 1 1 6 1 1 10 18 1 3 1 3 1 6 2 1 1 2 1 1 1 2 1 1 4 2 2 1 1 2 1 9 1 1 8 1 5 17 1 3 1 9 1 1 2 1 1 5 1 1 1 3 1 1 2 2 1 1 7 1 1 4 1 1 5 5 1 1 1 1 7 1 1 1 1 1 1 1 6 4 6 17 7 1 2 1 1 2 1 2 2 3 2 1 1 1 6 2 2 2 3 2 1 29 1 2 2 3 2 2 3 2 1 2 4 11 5 7 1 1 3 1 2 9 2 29 3 1 1 2 1 1 6 2 1 2 1 3 1 1 2 7 3 1 1 13 14 5 1 5 3 2 1 15 9 8 4 1 2 11 1 2 1 9 1 2 2 29 1 1 1 1 1 4 1 1 1 1 1 2 1 1 1 1 7 4 2 13 4 5 2 2 2 1 1 1 1 1 6 3 1 1 1 1 1 1 8 5 2 1 1 1 11 1 1 17 1 1 1 3 4 5 3 1 2 1 2 1 1 1 1 1 7 5 1 1 9 2 1 2 7 1 13 1 2 29 1 1 1 1 1 1 1 4 2 29 2 2 5 8 1 1 1 9 3 1 8 2 10 1 1 1 13 1 3 1 1 3 9 1 1 1 1 2 1 1 4 2 3 6 1 1 10 1 11 1 15 8 29 6 1 29 1 1 1 1 4 1 2 7 1 2 1 2 1 1 1 1 2 1 3 1 2 6 1 1 1 1 1 1 2 6 2 6 1 1 19 3 3 1 2 1 1 29 2 4 8 1 6 1 6 9 1 1 1 3 1 1 3 1 1 1 3 1 2 1 1 3 1 3 1 1 15 2 3 2 11 1 29 1 1 4 1 4 4 1 8 4 2 2 6 10 2 2 1 2 1 1 12 2 1 1 2 9 2 1 1 1 8 2 11 1 8 10 12 3 6 1 1 5 1 9 1 1 2 1 1 3 6 6 1 5 2 1 1 5 3 1 8 3 29 1 1 1 1 5 1 4 29 2 1 7 6 1 2 18 3 1 1 1 1 1 14 1 1 1 1 1 1 5 2 1 9 1 9 1 14 1 3 1 1 1 1 2 2 5 1 2 1 1 6 1 1 1 29 2 2 1 4 2 1 2 1 1 2 1 1 9 1 4 2 1 1 1 1 2 6 1 2 1 1 1 1 11 1 1 2 1 28 3 1 1 3 2 4 4 1 1 1 13 3 2 1 9 2 1 1 1 1 3 1 1 1 1 1 1 11 1 1 1 1 3 1 1 2 2 10 1 8 1 14 1 1 7 1 1 1 2 1 1 1 1 1 1 1 1 1 2 1 10 1 1 1 1 1 1 4 1 1 10 3 1 9 4 1 1 12 7 1 11 11 1 1 16 17 9 2 1 1 1 8 1 8 2 1 1 1 10 2 1 2 1 1 4 1 1 1 7 1 2 1 12 14 1 1 1 5 12 5 13 1 1 1 1 8 24 1 1 2 1 1 2 15 4 1 2 1 1 1 1 1 1 1 2 2 3 2 1 1 1 1 2 1 2 2 1 1 1 2 1 1 14 2 1 15 1 5 1 2 2 13 1 1 1 8 1 5 8 1 1 2 3 5 1 1 2 1 2 1 2 1 6 1 27 1 3 1 1 1 1 1 1 3 4 1 1 7 3 4 1 1 1 1 2 1 1 5 14 1 1 1 3 1 1 29 2 3 3 3 6 4 4 4 4 3 3 2 1 1 1 1 5 1 1 1 7 1 1 4 9 1 9 2 1 5 1 1 10 1 1 3 1 1 1 2 1 1 1 1 2 16 8 1 11 1 15 2 2 1 3 1 4 2 1 1 1 5 3 29 29 1 1 1 1 1 3 1 3 1 1 2 4 1 2 5 1 1 6 5 3 1 1 1 1 1 1 2 1 7 5 1 2 2 1 2 3 11 1 5 6 12 3 7 4 8 2 4 12 1 7 5 2 11 1 10 1 1 1 1 3 1 1 2 1 1 2 2 1 2 1 9 8 3 29 1 14 2 1 3 11 1 29 3 1 8 9 14 8 8 1 1 5 1 1 3 5 9 2 6 3 4 3 3 1 1 1 2 1 9 1 1 28 2 1 7 29 9 1 1 3 3 2 5 1 1 2 1 8 1 3 1 2 8 1 1 2 1 9 2 1 1 8 1 8 1 1 8 1 1 1 1 2 2 3 2 1 5 2 1 11 11 1 1 1 5 1 29 1 1 1 3 18 1 1 5 5 1 6 1 1 29 1 6 8 1 1 5 29 14 1 1 3 1 1 1 1 1 1 8 4 3 1 4 1 1 10 1 14 1 5 1 1 1 3 12 11 10 2 2 1 1 1 1 8 29 29 1 11 1 1 1 1 1 5 1 1 1 3 1 4 15 2 5 1 9 3 3 1 1 1 1 8 1 1 1 1 1 1 2 1 7 1 2 12 1 4 1 2 3 3 3 29 1 12 1 19 29 1 2 4 2 10 14 1 1 4 2 4 1 1 3 2 1 15 4 8 2 2 1 2 10 7 10 3 3 1 6 1 2 3 1 1 1 6 1 2 21 1 9 4 1 2 11 1 1 1 1 1 12 1 1 1 1 1 13 1 9 1 1 1 1 23 1 3 1 3 10 2 8 1 2 1 1 8 5 1 28 1 3 1 1 2 3 4 2 1 1 6 1 1 1 1 2 3 1 8 1 2 1 1 2 1 1 2 1 7 1 1 1 1 1 9 1 1 1 11 1 2 1 10 4 5 1 1 2 14 6 1 1 1 16 1 10 1 1 1 1 1 1 1 4 2 1 1 1 1 2 2 3 1 2 2 4 5 1 1 1 1 19 3 10 1 1 1 1 15 1 1 1 1 2 1 14 1 8 4 2 6 8 1 1 2 6 2 5 18 9 12 1 2 10 8 7 5 1 1 1 7 2 1 1 1 1 5 1 2 1 5 1 1 1 5 1 1 1 2 3 1 1 1 1 3 2 1 1 1 1 2 5 1 1 3 2 2 2 2 7 2 2 2 1 1 1 17 1 26 1 5 1 1 9 2 2 12 1 12 29 1 1 1 1 4 1 2 29 1 1 1 3 1 1 2 3 2 26 3 6 9 1 2 1 1 1 1 1 1 1 1 6 14 1 29 1 1 1 1 4 1 1 29 1 4 1 1 1 1 1 1 1 1 1 7 1 27 1 1 2 1 10 1 1 1 1 1 1 2 1 1 1 11

Databricks visualization. Run in Databricks to view.

+-------------+-----+
|num_languages|count|
+-------------+-----+
|            1|29666|
|            2| 7243|
|            3| 3723|
|            4| 2060|
|            5| 2036|
|            6| 1596|
|            7| 1289|
|            8| 1236|
|            9| 1219|
|           10| 1044|
|           11|  931|
|           12|  704|
|           13|  509|
|           14|  408|
|           15|  256|
|           16|  167|
|           17|  120|
|           18|  103|
|           19|   62|
|           20|   54|
+-------------+-----+
only showing top 20 rows



# 6. Analyse par genres

Les genres sont **centrales** pour Ubisoft :

- Ils décrivent le **positionnement gameplay** du jeu (Action, Adventure, RPG, Strategy…)
- Ils influencent :
  - le **public cible**,
  - la **plateforme privilégiée**,
  - la **probabilité de succès** (reviews, bouche-à-oreille),
  - la **concurrence**.

Dans cette section, on va :

1. Construire une table **explosée par genre** (`genres_exploded_df`)  
2. Analyser la **fréquence des genres**  
3. Mesurer la **satisfaction moyenne par genre** (`positive_rate`)  
4. Identifier les **genres “haut potentiel”** (volume + satisfaction)  
5. Étudier le lien **genres ↔ plateformes** (Windows / macOS / Linux)


In [0]:
# 6.1 Construction d'une table "un jeu = un genre" (explosion des genres)

# On découpe "genre_raw" en liste de genres, en gérant :
# - les séparateurs par virgule
# - les espaces éventuels après les virgules
games_df = games_df.withColumn(
    "genre_array",
    F.split(F.col("genre_raw"), r",\s*")
)

# Explosion : chaque ligne devient (jeu, genre_unique)
genres_exploded_df = (
    games_df
    .withColumn("genre", F.explode("genre_array"))
    .filter(F.col("genre").isNotNull() & (F.col("genre") != ""))
)

print("Table genres_exploded_df construite")
print("Nombre de lignes (jeu × genre) :", genres_exploded_df.count())
print("Nombre de genres uniques :", genres_exploded_df.select("genre").distinct().count())

genres_exploded_df.select(
    "name", "genre_raw", "genre", "price", "total_reviews", "positive_ratio"
).show(10, truncate=False)

Table genres_exploded_df construite
Nombre de lignes (jeu × genre) : 157110
Nombre de genres uniques : 28
+---------------------------+-----------------------------------+---------+------+-------------+------------------+
|name                       |genre_raw                          |genre    |price |total_reviews|positive_ratio    |
+---------------------------+-----------------------------------+---------+------+-------------+------------------+
|Counter-Strike             |Action                             |Action   |999.0 |206414       |0.9748127549487923|
|ASCENXION                  |Action, Adventure, Indie           |Action   |999.0 |32           |0.84375           |
|ASCENXION                  |Action, Adventure, Indie           |Adventure|999.0 |32           |0.84375           |
|ASCENXION                  |Action, Adventure, Indie           |Indie    |999.0 |32           |0.84375           |
|Crown Trick                |Adventure, Indie, RPG, Strategy    |Adventure|599.0 |

### 6.2 Genres les plus représentés

Objectifs :

- Repérer les **genres dominants** sur Steam  
- Identifier les **genres de niche**  
- Positionner Ubisoft par rapport aux tendances (AAA souvent Action / Adventure / RPG)

On calcule le **nombre de jeux distincts** par genre.

In [0]:
# 6.2 Comptage des jeux par genre

genre_counts_df = (
    genres_exploded_df
    .groupBy("genre")
    .agg(
        F.countDistinct("app_id").alias("nb_games")
    )
    .orderBy(F.desc("nb_games"))
)

print("Top 20 genres les plus représentés :")
genre_counts_df.show(20, truncate=False)

# Vue Databricks pour visualisation (bar chart)
display(genre_counts_df)

Top 20 genres les plus représentés :
+---------------------+--------+
|genre                |nb_games|
+---------------------+--------+
|Indie                |39681   |
|Action               |23759   |
|Casual               |22086   |
|Adventure            |21431   |
|Strategy             |10895   |
|Simulation           |10836   |
|RPG                  |9534    |
|Early Access         |6145    |
|Free to Play         |3393    |
|Sports               |2666    |
|Racing               |2155    |
|Massively Multiplayer|1460    |
|Utilities            |682     |
|Design & Illustration|406     |
|Animation & Modeling |322     |
|Education            |317     |
|Video Production     |247     |
|Audio Production     |195     |
|Violent              |168     |
|Software Training    |164     |
+---------------------+--------+
only showing top 20 rows



genre nb_games Indie 39681 Action 23759 Casual 22086 Adventure 21431 Strategy 10895 Simulation 10836 RPG 9534 Early Access 6145 Free to Play 3393 Sports 2666 Racing 2155 Massively Multiplayer 1460 Utilities 682 Design & Illustration 406 Animation & Modeling 322 Education 317 Video Production 247 Audio Production 195 Violent 168 Software Training 164 Game Development 159 Photo Editing 105 Gore 99 Web Publishing 89 Sexual Content 54 Nudity 45 Accounting 16 Movie 1

Databricks visualization. Run in Databricks to view.

### 6.3 Satisfaction par genre (ratio de reviews positives)

On cherche à répondre à :

- Quels genres ont les **meilleures évaluations moyennes** ?
- Quels genres combinent **volume** (nb de jeux, nb de reviews) et **satisfaction** ?

On agrège par genre :

- `sum_positive` : nombre total de reviews positives
- `sum_negative` : nombre total de reviews négatives
- `sum_total_reviews` : total des reviews
- `positive_rate` = `sum_positive / sum_total_reviews`

In [0]:
# 6.3 Agrégation des reviews par genre

genre_reviews_df = (
    genres_exploded_df
    .groupBy("genre")
    .agg(
        F.countDistinct("app_id").alias("nb_games"),
        F.sum("positive").alias("sum_positive"),
        F.sum("negative").alias("sum_negative"),
        F.sum("total_reviews").alias("sum_total_reviews")
    )
    .withColumn(
        "positive_rate",
        F.when(F.col("sum_total_reviews") > 0,
               F.col("sum_positive") / F.col("sum_total_reviews"))
         .otherwise(None)
    )
)

print("Aperçu brut des stats par genre :")
genre_reviews_df.select(
    "genre", "nb_games", "sum_total_reviews", "positive_rate"
).orderBy(F.desc("sum_total_reviews")).show(10)

Aperçu brut des stats par genre :
+--------------------+--------+-----------------+------------------+
|               genre|nb_games|sum_total_reviews|     positive_rate|
+--------------------+--------+-----------------+------------------+
|              Action|   23759|         64546277|0.8499114209174295|
|               Indie|   39681|         36772257|0.8846621244923857|
|           Adventure|   21431|         35342598|0.8400470446456709|
|        Free to Play|    3393|         23003053|0.8139026589209701|
|                 RPG|    9534|         22699856| 0.855755560740121|
|          Simulation|   10836|         17972902|0.8664371507728691|
|            Strategy|   10895|         15796295|0.8484818750219593|
|              Casual|   22086|         11572263|0.8671568387272222|
|Massively Multipl...|    1460|         10917738|0.7308361860304763|
|        Early Access|    6145|          5270786|0.8223811401183808|
+--------------------+--------+-----------------+------------------+


### 6.4 Genres “haut potentiel” (volume + satisfaction)

On définit un **seuil minimum de reviews** pour qu’un genre soit significatif.

Exemple :

- `MIN_REVIEWS_GENRE = 10 000` total (somme sur tous les jeux du genre)

Critères pour un genre “haut potentiel” :

- `sum_total_reviews >= MIN_REVIEWS_GENRE`
- `positive_rate >= 0.85` (85 % de reviews positives ou plus)
- un nombre suffisant de jeux (`nb_games`) pour être un genre durable

Cela permet de recommander à Ubisoft :

- des genres à **fort engagement**
- mais pas des genres “micro-niche”.

In [0]:
# 6.4 Sélection des genres "haut potentiel"

MIN_REVIEWS_GENRE = 10000

high_potential_genres_df = (
    genre_reviews_df
    .filter(F.col("sum_total_reviews") >= MIN_REVIEWS_GENRE)
    .filter(F.col("positive_rate") >= 0.85)
    .orderBy(F.desc("positive_rate"))
)

print(f"Genres 'haut potentiel' (≥ {MIN_REVIEWS_GENRE} reviews & ≥ 85% positives) :")
high_potential_genres_df.select(
    "genre", "nb_games", "sum_total_reviews", "positive_rate"
).show(20, truncate=False)

display(high_potential_genres_df)

Genres 'haut potentiel' (≥ 10000 reviews & ≥ 85% positives) :
+---------------------+--------+-----------------+------------------+
|genre                |nb_games|sum_total_reviews|positive_rate     |
+---------------------+--------+-----------------+------------------+
|Photo Editing        |105     |591496           |0.9767623111567957|
|Animation & Modeling |322     |717157           |0.9631991321286691|
|Design & Illustration|406     |701064           |0.9614771261967524|
|Utilities            |682     |782838           |0.9444291156024618|
|Game Development     |159     |30735            |0.8934764925980153|
|Indie                |39681   |36772257         |0.8846621244923857|
|Audio Production     |195     |78546            |0.8799684261451888|
|Video Production     |247     |127876           |0.8720479214238794|
|Casual               |22086   |11572263         |0.8671568387272222|
|Web Publishing       |89      |39222            |0.8664525011473153|
|Simulation           |10836

genre nb_games sum_positive sum_negative sum_total_reviews positive_rate Photo Editing 105 577751 13745 591496 0.9767623111567957 Animation & Modeling 322 690765 26392 717157 0.9631991321286691 Design & Illustration 406 674057 27007 701064 0.9614771261967524 Utilities 682 739335 43503 782838 0.9444291156024618 Game Development 159 27461 3274 30735 0.8934764925980153 Indie 39681 32531023 4241234 36772257 0.8846621244923857 Audio Production 195 69118 9428 78546 0.8799684261451888 Video Production 247 111514 16362 127876 0.8720479214238794 Casual 22086 10034967 1537296 11572263 0.8671568387272222 Web Publishing 89 33984 5238 39222 0.8664525011473153 Simulation 10836 15572390 2400512 17972902 0.8664371507728691 Racing 2155 2340353 383691 2724044 0.8591465482936399 RPG 9534 19425528 3274328 22699856 0.855755560740121

### 6.5 “Blockbusters” par genre : popularité × prix

On cherche un proxy simple de “potentiel business” par genre :

- Un jeu est considéré comme **“blockbuster-like”** s’il cumule :
  - beaucoup de reviews (`total_reviews` élevé)
  - un prix non nul (jeu payant)
  - un bon `positive_ratio`

On peut par exemple :

- filtrer les jeux avec `total_reviews > 50 000` et `positive_ratio > 0.9`
- regarder la répartition de ces jeux par genre

In [0]:
# 6.5 Jeux "blockbusters" et genres associés

blockbusters_df = (
    genres_exploded_df
    .filter(F.col("total_reviews") > 50000)
    .filter(F.col("positive_ratio") > 0.9)
    .filter(F.col("price") > 0)
)

print("Exemples de jeux 'blockbusters' (reviews >> 50k & >90% positives) :")
blockbusters_df.select(
    "name", "genre", "price", "total_reviews", "positive_ratio"
).distinct().show(20, truncate=False)

blockbuster_genre_counts = (
    blockbusters_df
    .groupBy("genre")
    .agg(
        F.countDistinct("app_id").alias("nb_blockbusters")
    )
    .orderBy(F.desc("nb_blockbusters"))
)

print("Genres les plus présents parmi les 'blockbusters' :")
blockbuster_genre_counts.show(20)

display(blockbuster_genre_counts)


Exemples de jeux 'blockbusters' (reviews >> 50k & >90% positives) :
+-----------------------------+------------+------+-------------+------------------+
|name                         |genre       |price |total_reviews|positive_ratio    |
+-----------------------------+------------+------+-------------+------------------+
|Ori and the Will of the Wisps|Action      |2999.0|93912        |0.9648181276088252|
|Terraria                     |Indie       |999.0 |1037091      |0.978420408623737 |
|Project Zomboid              |Simulation  |1999.0|131494       |0.9278446164844023|
|Project Zomboid              |Indie       |1999.0|131494       |0.9278446164844023|
|Arma 3                       |Strategy    |2999.0|232732       |0.9040398398157538|
|Arma 3                       |Simulation  |2999.0|232732       |0.9040398398157538|
|Arma 3                       |Action      |2999.0|232732       |0.9040398398157538|
|People Playground            |Simulation  |999.0 |144569       |0.988593681909676

genre nb_blockbusters Action 86 Indie 74 Adventure 59 Simulation 40 RPG 32 Strategy 31 Casual 15 Early Access 9 Racing 3 Sports 2 Massively Multiplayer 1 Animation & Modeling 1 Design & Illustration 1 Photo Editing 1 Utilities 1

Databricks visualization. Run in Databricks to view.

### 6.6 Genres × plateformes

Question clé pour Ubisoft :

> “Si on choisit un genre donné, doit-on viser Windows seul, ou aussi macOS / Linux ?”

On calcule, pour chaque genre :

- le nombre de jeux Windows
- le nombre de jeux Mac
- le nombre de jeux Linux

Cela permet d’identifier :

- les genres **historiquement PC “hardcore”** (ex : Strategy, Simulation, RPG → forte présence Linux)  
- les genres plus “casual / multi-plateformes” (Action, Casual, Indie…)

In [0]:
# 6.6 Croisement genres × plateformes

genre_platform_df = (
    genres_exploded_df
    .groupBy("genre")
    .agg(
        F.countDistinct("app_id").alias("nb_games"),
        F.sum(F.when(F.col("platform_windows") == True, 1).otherwise(0)).alias("nb_windows"),
        F.sum(F.when(F.col("platform_mac") == True, 1).otherwise(0)).alias("nb_mac"),
        F.sum(F.when(F.col("platform_linux") == True, 1).otherwise(0)).alias("nb_linux")
    )
    .orderBy(F.desc("nb_games"))
)

print("Genres × plateformes (top 30) :")
genre_platform_df.select(
    "genre", "nb_games", "nb_windows", "nb_mac", "nb_linux"
).show(30, truncate=False)

display(genre_platform_df)

Genres × plateformes (top 30) :
+---------------------+--------+----------+------+--------+
|genre                |nb_games|nb_windows|nb_mac|nb_linux|
+---------------------+--------+----------+------+--------+
|Indie                |39681   |39676     |9935  |6978    |
|Action               |23759   |23755     |4564  |3379    |
|Casual               |22086   |22082     |5130  |3305    |
|Adventure            |21431   |21427     |5039  |3302    |
|Strategy             |10895   |10892     |3005  |1826    |
|Simulation           |10836   |10832     |2439  |1532    |
|RPG                  |9534    |9533      |2248  |1524    |
|Early Access         |6145    |6145      |900   |632     |
|Free to Play         |3393    |3391      |845   |474     |
|Sports               |2666    |2665      |506   |287     |
|Racing               |2155    |2154      |424   |304     |
|Massively Multiplayer|1460    |1459      |270   |164     |
|Utilities            |682     |681       |102   |49      |
|Design 

genre nb_games nb_windows nb_mac nb_linux Indie 39681 39676 9935 6978 Action 23759 23755 4564 3379 Casual 22086 22082 5130 3305 Adventure 21431 21427 5039 3302 Strategy 10895 10892 3005 1826 Simulation 10836 10832 2439 1532 RPG 9534 9533 2248 1524 Early Access 6145 6145 900 632 Free to Play 3393 3391 845 474 Sports 2666 2665 506 287 Racing 2155 2154 424 304 Massively Multiplayer 1460 1459 270 164 Utilities 682 681 102 49 Design & Illustration 406 405 100 54 Animation & Modeling 322 322 74 38 Education 317 317 56 19 Video Production 247 247 29 6 Audio Production 195 193 41 7 Violent 168 168 33 22 Software Training 164 164 27 12 Game Development 159 159 52 35 Photo Editing 105 105 16 4 Gore 99 99 20 14 Web Publishing 89 89 20 8 Sexual Content 54 54 13 7 Nudity 45 45 10 7 Accounting 16 16 4 0 Movie 1 1 0 0

### 6.7 Synthèse – Genres pour Ubisoft

À partir de cette analyse, Ubisoft peut :

- **Cibler en priorité** :
  - des genres **fortement représentés** (pour toucher un marché large)
  - ET **bien notés** (positive_rate élevé)
  - ex. : *Action, Adventure, RPG, Strategy, Indie* (à valider avec les chiffres exacts)

- **Éviter** :
  - les genres sursaturés avec une satisfaction moyenne faible
  - les genres ultra-niche sans base marché suffisante

- **Penser multi-genres** :
  - de nombreux hits combinent plusieurs genres :  
    *Action + Adventure*, *RPG + Strategy*, *Indie + Puzzle*, etc.
  - Ubisoft peut se positionner sur un **mix de genres** plutôt qu’un seul “pur” genre.

# 7. Analyse détaillée des plateformes

Objectif : compléter la vision “macro” en regardant **plus finement** le rôle de chaque plateforme :

- Part de marché de Windows / macOS / Linux
- Part des jeux **exclusifs** vs **multi-plateformes**
- Qualité moyenne (reviews) par plateforme
- Pricing moyen par plateforme

Ces éléments sont cruciaux pour Ubisoft pour décider :
- s’il faut cibler uniquement Windows
- ou envisager des ports macOS / Linux.


In [0]:
# 7.1 Rappel des colonnes plateformes dans games_df

games_df.select(
    "name", "platform_windows", "platform_mac", "platform_linux"
).show(5)

+--------------------+----------------+------------+--------------+
|                name|platform_windows|platform_mac|platform_linux|
+--------------------+----------------+------------+--------------+
|      Counter-Strike|            true|        true|          true|
|           ASCENXION|            true|       false|         false|
|         Crown Trick|            true|       false|         false|
|Cook, Serve, Deli...|            true|        true|         false|
|            细胞战争|            true|       false|         false|
+--------------------+----------------+------------+--------------+
only showing top 5 rows



## 7.2 Répartition globale par plateforme

On calcule :

- le nombre de jeux disponibles sur chaque OS
- la part que cela représente dans le catalogue total.

In [0]:
total_games = games_df.count()

platform_agg_df = (
    games_df
    .agg(
        F.sum(F.when(F.col("platform_windows") == True, 1).otherwise(0)).alias("windows_count"),
        F.sum(F.when(F.col("platform_mac") == True, 1).otherwise(0)).alias("mac_count"),
        F.sum(F.when(F.col("platform_linux") == True, 1).otherwise(0)).alias("linux_count")
    )
)

platform_counts = platform_agg_df.collect()[0]
windows_count = platform_counts["windows_count"]
mac_count = platform_counts["mac_count"]
linux_count = platform_counts["linux_count"]

print("🎮 Répartition des jeux par plateforme :")
print(f"• Windows : {windows_count} ({windows_count / total_games * 100:.2f} %)")
print(f"• macOS   : {mac_count} ({mac_count / total_games * 100:.2f} %)")
print(f"• Linux   : {linux_count} ({linux_count / total_games * 100:.2f} %)")

platform_share_df = spark.createDataFrame(
    [
        ("Windows", int(windows_count), float(windows_count / total_games * 100)),
        ("macOS",   int(mac_count),    float(mac_count / total_games * 100)),
        ("Linux",   int(linux_count),  float(linux_count / total_games * 100)),
    ],
    ["platform", "nb_games", "share_percent"]
)

display(platform_share_df)
platform_share_df.show(5)

🎮 Répartition des jeux par plateforme :
• Windows : 55676 (99.97 %)
• macOS   : 12770 (22.93 %)
• Linux   : 8458 (15.19 %)


platform nb_games share_percent Windows 55676 99.97306566590652 macOS 12770 22.930096424916055 Linux 8458 15.187373184176977

+--------+--------+------------------+
|platform|nb_games|     share_percent|
+--------+--------+------------------+
| Windows|   55676| 99.97306566590652|
|   macOS|   12770|22.930096424916055|
|   Linux|    8458|15.187373184176977|
+--------+--------+------------------+



- Windows est **quasi universel** sur Steam
- macOS et Linux restent **très minoritaires**, mais non négligeables
- Ubisoft doit décider si le coût de portage vers macOS / Linux est justifié par ces parts.

## 7.3 Jeux exclusifs vs multi-plateformes

On distingue :

- `windows_only`   : uniquement Windows
- `windows_mac`    : Windows + macOS
- `windows_linux`  : Windows + Linux
- `tri_platform`   : Windows + macOS + Linux

Cela permet de voir si les jeux tendent à être **multi-plateformes** ou non.

In [0]:
games_df = (
    games_df
    .withColumn(
        "is_windows_only",
        (F.col("platform_windows") == True) &
        (F.col("platform_mac") == False) &
        (F.col("platform_linux") == False)
    )
    .withColumn(
        "is_tri_platform",
        (F.col("platform_windows") == True) &
        (F.col("platform_mac") == True) &
        (F.col("platform_linux") == True)
    )
    .withColumn(
        "is_windows_mac",
        (F.col("platform_windows") == True) &
        (F.col("platform_mac") == True) &
        (F.col("platform_linux") == False)
    )
    .withColumn(
        "is_windows_linux",
        (F.col("platform_windows") == True) &
        (F.col("platform_mac") == False) &
        (F.col("platform_linux") == True)
    )
)

platform_profile_df = (
    games_df
    .agg(
        F.sum(F.when(F.col("is_windows_only"), 1).otherwise(0)).alias("windows_only"),
        F.sum(F.when(F.col("is_tri_platform"), 1).otherwise(0)).alias("tri_platform"),
        F.sum(F.when(F.col("is_windows_mac"), 1).otherwise(0)).alias("windows_mac"),
        F.sum(F.when(F.col("is_windows_linux"), 1).otherwise(0)).alias("windows_linux")
    )
)

display(platform_profile_df)
platform_profile_df.show(5, truncate=False)

windows_only tri_platform windows_mac windows_linux 41271 6807 5951 1647

+------------+------------+-----------+-------------+
|windows_only|tri_platform|windows_mac|windows_linux|
+------------+------------+-----------+-------------+
|41271       |6807        |5951       |1647         |
+------------+------------+-----------+-------------+



- Une grande partie des jeux restent **Windows-only**, souvent pour des raisons de coût.
- Le véritable “premium segment” technique correspond aux jeux **tri-plateformes**.
- C’est ce segment que Ubisoft vise en général avec ses AAA (qualité d’optimisation élevée).

## 7.4 Qualité & popularité moyenne par plateforme

On veut savoir :

- Les jeux Windows-only sont-ils **mieux ou moins bien notés** que les tri-plateformes ?
- Les jeux multiplateformes ont-ils tendance à avoir **plus de reviews** (donc plus de visibilité) ?

In [0]:
# On crée une colonne catégorie de plateforme lisible

games_df = games_df.withColumn(
    "platform_profile",
    F.when(F.col("is_tri_platform"), F.lit("Windows + macOS + Linux"))
     .when(F.col("is_windows_mac"), F.lit("Windows + macOS"))
     .when(F.col("is_windows_linux"), F.lit("Windows + Linux"))
     .when(F.col("is_windows_only"), F.lit("Windows only"))
     .otherwise(F.lit("Others"))
)

platform_quality_df = (
    games_df
    .groupBy("platform_profile")
    .agg(
        F.countDistinct("app_id").alias("nb_games"),
        F.avg("positive_ratio").alias("avg_positive_ratio"),
        F.avg("total_reviews").alias("avg_total_reviews"),
        F.avg("price").alias("avg_price")
    )
    .orderBy(F.desc("nb_games"))
)

display(platform_quality_df)
platform_quality_df.show(10, truncate=False)

platform_profile nb_games avg_positive_ratio avg_total_reviews avg_price Windows only 41271 0.7222222678001455 1251.8536018027187 776.2599646240702 Windows + macOS + Linux 6807 0.7831160221396127 4547.496253856324 809.5802850007345 Windows + macOS 5951 0.7704985585348048 1784.441774491682 740.5088220467148 Windows + Linux 1647 0.7816311294761643 1300.7844565877353 654.4116575591985 Others 15 0.5346832842570547 70.26666666666667 2172.8

+-----------------------+--------+------------------+------------------+-----------------+
|platform_profile       |nb_games|avg_positive_ratio|avg_total_reviews |avg_price        |
+-----------------------+--------+------------------+------------------+-----------------+
|Windows only           |41271   |0.7222222678001455|1251.8536018027187|776.2599646240702|
|Windows + macOS + Linux|6807    |0.7831160221396127|4547.496253856324 |809.5802850007345|
|Windows + macOS        |5951    |0.7704985585348048|1784.441774491682 |740.5088220467148|
|Windows + Linux        |1647    |0.7816311294761643|1300.7844565877353|654.4116575591985|
|Others                 |15      |0.5346832842570547|70.26666666666667 |2172.8           |
+-----------------------+--------+------------------+------------------+-----------------+



**Points à commenter** :

- Les jeux **tri-plateformes** ont en général :
  - un **volume de reviews plus élevé** (plus d’audience),
  - un **niveau de qualité moyen élevé** (positive_ratio).
- Les jeux **Windows-only** peuvent être plus “expérimentaux” / “indie”, avec plus de variance.

Ubisoft, positionné sur du AAA, est naturellement attendu dans la catégorie
**“Windows + macOS + Linux”**, ou à minima **“Windows + macOS”**.

## 7.5 Top jeux par plateforme (exemples concrets à citer)

On extrait quelques jeux emblématiques par profil de plateforme

In [0]:
# Windows only – quelques exemples
top_windows_only = (
    games_df
    .filter("is_windows_only = true")
    .orderBy(F.desc("total_reviews"))
    .select("name", "price", "total_reviews", "positive_ratio")
    .limit(10)
)

print("Exemples de jeux populaires 'Windows only' :")
top_windows_only.show(10, truncate=False)

# Tri-plateformes – quelques exemples
top_tri_platform = (
    games_df
    .filter("is_tri_platform = true")
    .orderBy(F.desc("total_reviews"))
    .select("name", "price", "total_reviews", "positive_ratio")
    .limit(10)
)

print("Exemples de jeux populaires 'Windows + macOS + Linux' :")
top_tri_platform.show(10, truncate=False)

Exemples de jeux populaires 'Windows only' :
+------------------------------+------+-------------+------------------+
|name                          |price |total_reviews|positive_ratio    |
+------------------------------+------+-------------+------------------+
|PUBG: BATTLEGROUNDS           |0.0   |2093876      |0.5661084992616564|
|Grand Theft Auto V            |2998.0|1442644      |0.852091714934523 |
|Tom Clancy's Rainbow Six Siege|1999.0|1086157      |0.8681157512219688|
|The Witcher 3: Wild Hunt      |3999.0|657872       |0.9616262738040227|
|Among Us                      |499.0 |638716       |0.9179384890937443|
|Dead by Daylight              |1999.0|626034       |0.8140723986237169|
|Wallpaper Engine              |399.0 |572127       |0.9807193158162436|
|Rocket League                 |0.0   |559544       |0.8873278955721087|
|Cyberpunk 2077                |5999.0|557109       |0.7664622183450636|
|ELDEN RING                    |5999.0|542271       |0.9039815885415226|
+-----

### 7.6 Synthèse – Plateformes & stratégie Ubisoft


- **Windows est incontournable** : quasi tout le catalogue Steam l’utilise.
- macOS et Linux représentent des parts **plus petites mais non négligeables**, surtout sur les genres “hardcore” (Strategy, Simulation, RPG, Indie).
- Les jeux **multi-plateformes** (notamment tri-plateformes) sont souvent :
  - plus visibles (plus de reviews),
  - mieux optimisés,
  - perçus comme plus “premium”.

**Recommandation pour Ubisoft :**

> Viser en priorité **Windows + macOS**, avec un port Linux si le jeu cible un public “PC enthusiast” (Strategy / Simulation / RPG), cohérent avec l’ADN Steam.

# 8. Analyse des Prix & Promotions

Dans cette section, nous analysons les prix réels des jeux (en euros)  
à partir des colonnes :

- `price_eur`
- `initialprice_eur`
- `discount`

Objectifs :

1. Distribution des prix (EUR)  
2. Aperçu des promotions  
3. Variations de prix selon les genres  
4. Lien prix ↔ succès (reviews)  
5. Effets COVID sur les prix

In [0]:
# Vérification rapide
games_df.select("name", "price_eur", "initialprice_eur", "discount").show(5)

+--------------------+---------+----------------+--------+
|                name|price_eur|initialprice_eur|discount|
+--------------------+---------+----------------+--------+
|      Counter-Strike|     9.99|            9.99|     0.0|
|           ASCENXION|     9.99|            9.99|     0.0|
|         Crown Trick|     5.99|           19.99|    70.0|
|Cook, Serve, Deli...|    19.99|           19.99|     0.0|
|            细胞战争|     1.99|            1.99|     0.0|
+--------------------+---------+----------------+--------+
only showing top 5 rows



## 8.1 Distribution réelle des prix (en euros)

Caractéristiques principales observées :

- Prix minimum : **0,28 €**
- Médiane : **5,99 €**
- Moyenne : **8,99 €**
- 75% : **10,00 €**
- Maximum : **999,00 €**

Ainsi, une large majorité des jeux vendus sur Steam se positionnent entre :
**0,99 € et 9,99 €**.

Les prix extrêmes (> 200 €) correspondent à :
- bundles
- logiciels (vidéo, 3D…)
- packs premium multi-DLC

In [0]:
# Statistiques en euros
price_stats = games_df.select("price_eur").summary()
display(price_stats)

summary price_eur count 55691 mean 7.732849832104521 stddev 10.931345827234507 min 0.0 25% 1.29 50% 4.99 75% 9.99 max 999.0


- Le marché Steam est dominé par les **petits jeux low-cost**.
- Les prix “mass market” se situent entre **5 € et 15 €**.
- Ubisoft, positionné AAA, vise plutôt une fourchette entre **20 € et 60 €**.

Le dataset permet donc de comprendre la structure du marché mais  
pas de comparer directement les AAA (rarement présents dans les données).

## 8.2 Jeux en promotion (discount > 0)

Nous observons la proportion de jeux qui appliquent des promotions.

In [0]:
discount_count = games_df.filter(F.col("discount") > 0).count()
total_games = games_df.count()

print(f"Jeux en promotion : {discount_count} / {total_games} "
      f"({discount_count/total_games*100:.2f}%)")

display(
    games_df.filter("discount > 0")
            .select("name", "price_eur", "initialprice_eur", "discount")
            .limit(20)
)

Jeux en promotion : 2518 / 55691 (4.52%)


name price_eur initialprice_eur discount Crown Trick 5.99 19.99 70.0 Zengeon 7.99 19.99 60.0 The Far Kingdoms: Elements 3.49 4.99 30.0 Tools Up! 5.99 19.99 70.0 WRC 8 FIA World Rally Championship 5.99 29.99 80.0 Tetsumo Party 1.49 4.99 70.0 PUZZLE: BIRDS 0.31 0.99 69.0 Trouble Travel TT 0.54 0.99 45.0 Stage of Light 11.24 14.99 25.0 The Trials of Olympus II: Wrath of the Gods 4.89 6.99 30.0 Golf Pool VR 4.99 9.99 50.0 Shards of Infinity 5.59 7.99 30.0 Tales of Sorrow: Strawsbrough Town 2.59 3.99 35.0 PASHTET 0.41 2.99 86.0 The Princess, the Stray Cat, and Matters of the Heart 9.99 19.99 50.0 Wings of Glass 玻璃の羽 1.79 5.99 70.0 HENTAI MINESWEEPER 0.99 1.99 50.0 UNI 0.99 4.99 80.0 Walden, a game 4.99 9.99 50.0 Soccering 0.44 0.99 56.0

### Commentaire :

- Environ **1 jeu sur 3** applique une promotion.
- Steam habitue sa communauté à acheter en Soldes.
- Un jeu Ubisoft doit intégrer une stratégie :
  - lancement **à plein tarif**
  - premières promotions **modérées** (-10% à -25%)
  - grosses promotions en période de Soldes Steam (-40% à -60%)

## 8.3 Prix par genre

In [0]:
price_by_genre_df = (
    genres_exploded_df
    .groupBy("genre")
    .agg(
        F.count("*").alias("nb_games"),
        F.avg("price_eur").alias("avg_price_eur"),
        F.expr("percentile(price_eur, 0.5)").alias("median_price_eur")
    )
    .orderBy(F.desc("median_price_eur"))
)

display(price_by_genre_df)
price_by_genre_df.show(10)

genre nb_games avg_price_eur median_price_eur Web Publishing 89 21.796292134831468 11.99 Software Training 164 19.032682926829207 11.49 Game Development 159 21.282201257861583 9.99 Early Access 6145 8.748242473555463 6.99 Audio Production 195 19.644974358974302 5.99 Design & Illustration 406 19.058374384236348 5.99 Photo Editing 105 20.326190476190476 5.99 RPG 9534 9.042684078037091 5.99 Simulation 10836 9.091596530086097 5.99 Education 317 14.341703470031465 4.99 Sexual Content 54 6.875185185185189 4.99 Adventure 21431 8.006242825812555 4.99 Sports 2666 8.947970742686014 4.99 Racing 2155 8.221090487238936 4.99 Nudity 45 6.958888888888895 4.99 Action 23759 7.727079843426779 4.99 Strategy 10895 8.404957319872398 4.99 Indie 39681 6.5681399158259515 4.99 Animation & Modeling 322 18.776304347826013 3.99 Gore 99 5.700606060606066 3.99 Utilities 682 11.450425219941243 3.99 Violent 168 5.27958333333334 3.99 Casual 22086 5.606983156752638 3.99 Video Production 247 18.95890688259103 2.99 Accounting 16 14.432500000000001 0.995 Massively Multiplayer 1460 5.00023972602733 0.0 Movie 1 0.0 0.0 Free to Play 3393 0.28656940760389066 0.0

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

+--------------------+--------+------------------+----------------+
|               genre|nb_games|     avg_price_eur|median_price_eur|
+--------------------+--------+------------------+----------------+
|      Web Publishing|      89|21.796292134831468|           11.99|
|   Software Training|     164|19.032682926829207|           11.49|
|    Game Development|     159|21.282201257861583|            9.99|
|        Early Access|    6145| 8.748242473555463|            6.99|
|Design & Illustra...|     406|19.058374384236348|            5.99|
|    Audio Production|     195|19.644974358974302|            5.99|
|       Photo Editing|     105|20.326190476190476|            5.99|
|                 RPG|    9534| 9.042684078037091|            5.99|
|          Simulation|   10836| 9.091596530086097|            5.99|
|              Sports|    2666| 8.947970742686014|            4.99|
+--------------------+--------+------------------+----------------+
only showing top 10 rows




Genres les **plus chers** (médiane la plus élevée) :

- RPG
- Simulation
- Strategy
- Racing

→ Jeux complexes, souvent premium.

Genres **moins chers** :

- Indie
- Casual
- Free to Play

→ Cibles grand public, modèle low-cost.

Ubisoft se positionne naturellement dans :
**Action / Adventure / RPG / Strategy**,  
donc dans la partie “premium” du marché

## 8.4 Prix ↔ Succès (reviews)

In [0]:
price_success_df = (
    games_df
    .select("price_eur", "total_reviews", "positive_ratio")
    .filter("total_reviews > 0 AND price_eur > 0")
)

display(price_success_df)

price_eur total_reviews positive_ratio 9.99 206414 0.9748127549487923 9.99 32 0.84375 5.99 4678 0.8619067977768277 19.99 1690 0.9319526627218935 1.99 1 0.0 7.99 1480 0.6878378378378378 12.99 24 0.75 2.99 6 1.0 13.99 44 0.7272727272727273 0.99 6 0.16666666666666666 16.99 4346 0.9275195582144501 24.99 1540 0.787012987012987 4.99 68 0.8088235294117647 9.99 15 0.6 6.99 12 0.75 9.99 115 0.9304347826086956 2.99 7 1.0 19.99 5 1.0 11.99 94 0.5851063829787234 0.99 10 0.6 14.99 6 0.8333333333333334 0.99 166 0.9759036144578314 4.99 59 0.6779661016949152 7.99 10 0.5 3.99 1 0.0 1.98 1 1.0 6.99 1 1.0 6.99 11 0.7272727272727273 1.99 12 0.75 19.99 105 0.6285714285714286 0.99 131 0.8473282442748091 15.99 12 1.0 14.99 291 0.9072164948453608 0.99 15 0.8666666666666667 12.99 33 0.9090909090909091 19.99 23 0.43478260869565216 10.99 8 0.25 6.99 17 1.0 1.99 2 0.5 6.99 14 0.5714285714285714 5.99 8 0.75 4.99 2 1.0 4.99 9 1.0 4.99 34 0.9411764705882353 9.99 58 0.39655172413793105 9.99 11 1.0 2.99 1 1.0 4.99 4 1.0 16.99 459 0.8278867102396514 9.99 30 0.9666666666666667 1.99 56 0.8214285714285714 1.99 10 0.6 7.99 21 0.5714285714285714 8.99 30 0.9333333333333333 12.99 101 0.7920792079207921 3.99 5 0.2 0.99 83 0.6987951807228916 14.99 33 0.8787878787878788 14.99 60 0.45 0.99 9 0.6666666666666666 8.99 16 0.625 2.99 23 0.9565217391304348 0.99 55 0.8909090909090909 3.49 28 0.6785714285714286 9.99 8 0.75 0.99 72 0.8333333333333334 16.99 20 0.55 7.99 10 0.7 19.99 178 0.9382022471910112 7.99 14 0.7857142857142857 0.99 25 0.56 5.99 1 1.0 4.99 23 1.0 2.99 6 0.8333333333333334 9.99 18 0.7777777777777778 3.99 3288 0.9562043795620438 3.99 4 0.75 3.99 4 1.0 1.99 60 0.7333333333333333 4.99 7 0.5714285714285714 4.99 5 0.6 11.99 3 0.3333333333333333 1.99 15 0.9333333333333333 3.99 33 0.696969696969697 7.99 3 1.0 9.99 4 1.0 4.99 1 0.0 0.99 48 0.7708333333333334 2.99 18 0.7777777777777778 1.99 8 1.0 29.99 30 0.9666666666666667 0.99 39 0.6666666666666666 14.99 881 0.8456299659477866 14.99 115 0.7478260869565218 9.99 8 0.125 5.99 18 0.8888888888888888 9.99 13 0.8461538461538461 1.99 7 0.7142857142857143 9.99 692 0.7514450867052023 24.99 29 0.6896551724137931 14.99 27 0.7777777777777778 0.99 528 0.8920454545454546 4.99 54 0.7962962962962963 1.99 1532 0.8714099216710183 0.99 5 0.0 14.99 16 0.6875 39.99 4346 0.9590427979751496 0.99 23 0.9130434782608695 0.99 4 0.0 6.99 4 0.25 9.99 1 1.0 9.99 44 0.9545454545454546 3.99 146 0.9178082191780822 10.99 2 1.0 0.99 2 0.5 7.99 26 0.9615384615384616 39.99 3987 0.8457486832204665 4.99 1 1.0 59.99 82 0.6951219512195121 1.99 29 0.6896551724137931 2.99 11 0.9090909090909091 0.99 18 0.2777777777777778 5.99 5 0.4 16.99 52 0.9423076923076923 6.99 1 1.0 7.99 2 0.0 9.99 26 0.5769230769230769 1.99 129 0.937984496124031 4.99 11 0.9090909090909091 0.99 541 0.9648798521256932 14.99 1443 0.6936936936936937 2.99 5 1.0 2.99 354 0.940677966101695 0.99 2 0.5 19.99 32 0.71875 5.99 834 0.7541966426858513 4.99 21 0.7619047619047619 18.99 46 0.9130434782608695 0.99 17 0.35294117647058826 2.99 78 0.6923076923076923 0.99 3 0.6666666666666666 0.99 9 0.7777777777777778 4.99 288 0.8888888888888888 19.99 52 0.8269230769230769 3.99 36 0.9722222222222222 7.99 96 0.8541666666666666 5.99 939 0.7305644302449414 12.99 550 0.9836363636363636 2.99 4 0.5 5.99 1 1.0 14.99 143 0.8881118881118881 5.99 37 0.9459459459459459 12.99 47 0.8936170212765957 12.99 33 0.8484848484848485 11.99 8 0.875 12.99 105 0.8095238095238095 2.99 5 0.8 29.99 2413 0.9535847492747617 3.99 24 1.0 0.99 1 1.0 14.99 202 0.9504950495049505 7.99 120 0.9333333333333333 9.99 63 0.9682539682539683 15.99 327 0.8073394495412844 1.5 7 0.8571428571428571 8.99 13 0.6153846153846154 24.99 24 0.3333333333333333 1.99 20 0.6 2.99 21 0.8095238095238095 5.99 2 0.5 4.99 1 0.0 14.99 11 0.8181818181818182 0.99 39 0.9230769230769231 11.99 15 1.0 9.99 1344 0.9449404761904762 1.49 13 0.8461538461538461 24.99 20 0.8 1.99 29 0.5517241379310345 9.99 9 1.0 0.99 15 0.3333333333333333 0.99 1 1.0 4.99 109 0.9174311926605505 0.99 124

### Interprétation :


- Les jeux entre **5 € et 20 €** génèrent **le plus de reviews**.
- Les jeux très chers (> 40 €) ont peu de reviews → ils ne sont pas leaders.
- Les blockbusters (ex : Terraria, Project Zomboid) sont autour de **9,99 € – 19,99 €**.

## 8.5 Prix moyen par période COVID


In [0]:
covid_price_df = (
    games_df
    .groupBy("covid_period")
    .agg(
        F.count("*").alias("nb_games"),
        F.avg("price_eur").alias("avg_price_eur"),
        F.avg("discount").alias("avg_discount")
    )
)

display(covid_price_df)
covid_price_df.show()

covid_period nb_games avg_price_eur avg_discount pre_covid 23977 7.1507519706375815 2.6003670183926264 unknown 222 6.735810810810815 1.4639639639639639 covid 24041 7.709633126741579 2.5445696934403728 post_covid 7451 9.710632129915007 2.839753053281439

+------------+--------+------------------+------------------+
|covid_period|nb_games|     avg_price_eur|      avg_discount|
+------------+--------+------------------+------------------+
|   pre_covid|   23977|7.1507519706375815|2.6003670183926264|
|     unknown|     222| 6.735810810810815|1.4639639639639639|
|       covid|   24041| 7.709633126741579|2.5445696934403728|
|  post_covid|    7451| 9.710632129915007| 2.839753053281439|
+------------+--------+------------------+------------------+



### Commentaire final :

- Pendant la période **COVID (2019–2021)**, les sorties ont explosé (+24 000 jeux),
  mais les **prix moyens sont restés stables**.
- Les studios indie ont “inondé” Steam d’offres low-cost.
- Ubisoft peut se différencier par :
  - **la qualité**
  - **la profondeur**
  - **le cross-platform**
  - **un pricing premium maîtrisé**

# 9. Insights Business pour Ubisoft 
Analyse stratégique basée sur les données Steam

Dans cette section, on synthétise les enseignements majeurs du marché Steam
afin de proposer des recommandations concrètes pour Ubisoft.

Ces insights s’appuient sur :

l’analyse des genres (Section 6)

les prix & promotions (Section 8)

les tendances annuelles & COVID (Section 5)

les plateformes (Section 5.1 et 6.6)

les blockbusters (Section 6.5)

Insight 1 — Steam est dominé par les jeux Indie & Action

(mais les blockbusters restent concentrés dans les genres premium)

Ce que disent les données :

Top genres les plus présents :

Indie (39 681 jeux)

Action (23 759 jeux)

Casual (22 086 jeux)

Adventure (21 431 jeux)

Les Indies représentent 40–45 % du catalogue → marché saturé.

Mais côté blockbusters (> 50k reviews + > 90% positives) :
Genre	Nb blockbusters
Action	86
Indie	74
Adventure	59
Simulation	40
RPG	32
Strategy	31

-- Les blockbusters se concentrent sur les six mêmes genres que ceux d’Ubisoft. -->
-- Donc Ubisoft reste aligné avec la zone “haut potentiel”, pas la zone low-cost.

Recommandation Ubisoft

✔ Continuer à viser : Action / Adventure / RPG / Strategy / Simulation

✔ Positionnement premium = cohérent avec les genres qui génèrent le plus de succès

✔ Investir dans des mécaniques hybrides :

  . Action + Survival

  . RPG + Strategy

  . Simulation + Narrative